In [1]:
import ipdb # alternative to pdb that works in jupyter notebook (pip3 install ipdb)
import os, subprocess, sys, re, time
from pathlib import Path
from pynq import Overlay   
from pynq import allocate
from threading import Thread, Lock
#from pynq import GPIO

BASE_DIR = Path('/home/xilinx/Django/pynq')

PATH = BASE_DIR / 'tools/make'

base = Overlay(str(BASE_DIR / 'dma_test.bit'))
#base = Overlay(str(BASE_DIR / 'onboard.bit'))

dma_rec = base.axi_dma_0.recvchannel
dma_send = base.axi_dma_0.sendchannel

def print_dma_channel_status(channel, name='dma'):
    print(f'{name}.running =', channel.running)
    print(f'{name}.idle =', channel.idle)
    print(f'{name}.error =', channel.error)
    print(f'status =', hex(channel._mmio.read(channel._offset + 4)))
    
def print_dma_channels_status():
    print_dma_channel_status(dma_rec, name='dma_rec')
    print()
    print_dma_channel_status(dma_send, name='dma_send')

gpio_counts = base.axi_gpio_counts
gpio_flags = base.axi_gpio_flags

def print_flags():
    print('almost_empty =', gpio_flags[0].read())
    print('prog_empty =', gpio_flags[1].read())
    print('almost_full =', gpio_flags[2].read())
    print('prog_full =', gpio_flags[3].read())
    
write_count_channel = gpio_counts.channel1
read_count_channel = gpio_counts.channel2
def read_count():
    print('read count =', read_count_channel.read())
def write_count():
    print('write count =', write_count_channel.read())

input_buffer_lock = Lock()
input_buffer = allocate(shape=(16,), dtype='u8')
output_buffer = allocate(shape=(16,), dtype='u8')

def print_buffers():
    #print('input_buffer =', ', '.join(f'{i:08X}' for i in input_buffer))
    #print('output_buffer =', ', '.join(f'{i:08X}' for i in output_buffer))
    with input_buffer_lock:
        print('input_buffer =', input_buffer)
    print('output_buffer =', output_buffer)

def print_stats():
    read_count()
    write_count()
    print_flags()
    print()
    print_dma_channels_status()
    print_buffers()
    print()

In [2]:
print_stats()

read count = 0
write count = 0
almost_empty = 1
prog_empty = 1
almost_full = 0
prog_full = 0

dma_rec.running = True
dma_rec.idle = False
dma_rec.error = False
status = 0x0

dma_send.running = True
dma_send.idle = False
dma_send.error = False
status = 0x0
input_buffer = [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
output_buffer = [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]



In [12]:
output_buffer[:] = [i+0x0 for i in range(1, len(output_buffer)+1)]
dma_send.transfer(output_buffer, nbytes=8)
dma_send.wait()
print_stats()

read count = 0
write count = 0
almost_empty = 1
prog_empty = 1
almost_full = 0
prog_full = 0

dma_rec.running = True
dma_rec.idle = True
dma_rec.error = False
status = 0x1002

dma_send.running = True
dma_send.idle = True
dma_send.error = False
status = 0x1002
input_buffer = [1 2 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
output_buffer = [ 1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16]

dma_rec.wait completed
dma_rec.transfer
dma_rec.transfer returned
dma_rec.wait completed
dma_rec.transfer
dma_rec.transfer returned


In [8]:
with input_buffer_lock:
    dma_rec.transfer(input_buffer, nbytes=16)
dma_rec.wait()
print_stats()

read count = 0
write count = 0
almost_empty = 1
prog_empty = 1
almost_full = 0
prog_full = 0

dma_rec.running = True
dma_rec.idle = True
dma_rec.error = False
status = 0x1002

dma_send.running = True
dma_send.idle = True
dma_send.error = False
status = 0x1002
input_buffer = [1 2 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
output_buffer = [ 1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16]



In [3]:

def rec(x, ib):
    while True:
        print('dma_rec.transfer')
        with input_buffer_lock:
            x.transfer(ib, nbytes=16)
        print('dma_rec.transfer returned')
        x.wait()
        time.sleep(1)
        print('dma_rec.wait completed')
    
Thread(target=rec, args=[dma_rec, input_buffer], daemon=True).start()

dma_rec.transfer
dma_rec.transfer returned


In [3]:
base.axi_dma_0.register_map

RegisterMap {
  MM2S_DMACR = Register(RS=1, Reset=0, Keyhole=0, Cyclic_BD_Enable=0, IOC_IrqEn=0, Dly_IrqEn=0, Err_IrqEn=0, IRQThreshold=1, IRQDelay=0),
  MM2S_DMASR = Register(Halted=0, Idle=0, SGIncld=0, DMAIntErr=0, DMASlvErr=0, DMADecErr=0, SGIntErr=0, SGSlvErr=0, SGDecErr=0, IOC_Irq=0, Dly_Irq=0, Err_Irq=0, IRQThresholdSts=0, IRQDelaySts=0),
  MM2S_CURDESC = Register(Current_Descriptor_Pointer=0),
  MM2S_CURDESC_MSB = Register(Current_Descriptor_Pointer=0),
  MM2S_TAILDESC = Register(Tail_Descriptor_Pointer=0),
  MM2S_TAILDESC_MSB = Register(Tail_Descriptor_Pointer=0),
  MM2S_SA = Register(Source_Address=0),
  MM2S_SA_MSB = Register(Source_Address=0),
  MM2S_LENGTH = Register(Length=0),
  SG_CTL = Register(SG_CACHE=0, SG_USER=0),
  S2MM_DMACR = Register(RS=1, Reset=0, Keyhole=0, Cyclic_BD_Enable=0, IOC_IrqEn=0, Dly_IrqEn=0, Err_IrqEn=0, IRQThreshold=1, IRQDelay=0),
  S2MM_DMASR = Register(Halted=0, Idle=0, SGIncld=0, DMAIntErr=0, DMASlvErr=0, DMADecErr=0, SGIntErr=0, SGSlvErr=0, SG

In [6]:
base.axi_dma_0.register_map

RegisterMap {
  MM2S_DMACR = Register(RS=1, Reset=0, Keyhole=0, Cyclic_BD_Enable=0, IOC_IrqEn=0, Dly_IrqEn=0, Err_IrqEn=0, IRQThreshold=1, IRQDelay=0),
  MM2S_DMASR = Register(Halted=0, Idle=1, SGIncld=0, DMAIntErr=0, DMASlvErr=0, DMADecErr=0, SGIntErr=0, SGSlvErr=0, SGDecErr=0, IOC_Irq=1, Dly_Irq=0, Err_Irq=0, IRQThresholdSts=0, IRQDelaySts=0),
  MM2S_CURDESC = Register(Current_Descriptor_Pointer=0),
  MM2S_CURDESC_MSB = Register(Current_Descriptor_Pointer=0),
  MM2S_TAILDESC = Register(Tail_Descriptor_Pointer=0),
  MM2S_TAILDESC_MSB = Register(Tail_Descriptor_Pointer=0),
  MM2S_SA = Register(Source_Address=922959872),
  MM2S_SA_MSB = Register(Source_Address=0),
  MM2S_LENGTH = Register(Length=8),
  SG_CTL = Register(SG_CACHE=0, SG_USER=0),
  S2MM_DMACR = Register(RS=1, Reset=0, Keyhole=0, Cyclic_BD_Enable=0, IOC_IrqEn=0, Dly_IrqEn=0, Err_IrqEn=0, IRQThreshold=1, IRQDelay=0),
  S2MM_DMASR = Register(Halted=0, Idle=0, SGIncld=0, DMAIntErr=0, DMASlvErr=0, DMADecErr=0, SGIntErr=0, SGSlvE

In [9]:
base.axi_dma_0.register_map

RegisterMap {
  MM2S_DMACR = Register(RS=1, Reset=0, Keyhole=0, Cyclic_BD_Enable=0, IOC_IrqEn=0, Dly_IrqEn=0, Err_IrqEn=0, IRQThreshold=1, IRQDelay=0),
  MM2S_DMASR = Register(Halted=0, Idle=1, SGIncld=0, DMAIntErr=0, DMASlvErr=0, DMADecErr=0, SGIntErr=0, SGSlvErr=0, SGDecErr=0, IOC_Irq=1, Dly_Irq=0, Err_Irq=0, IRQThresholdSts=0, IRQDelaySts=0),
  MM2S_CURDESC = Register(Current_Descriptor_Pointer=0),
  MM2S_CURDESC_MSB = Register(Current_Descriptor_Pointer=0),
  MM2S_TAILDESC = Register(Tail_Descriptor_Pointer=0),
  MM2S_TAILDESC_MSB = Register(Tail_Descriptor_Pointer=0),
  MM2S_SA = Register(Source_Address=922959872),
  MM2S_SA_MSB = Register(Source_Address=0),
  MM2S_LENGTH = Register(Length=8),
  SG_CTL = Register(SG_CACHE=0, SG_USER=0),
  S2MM_DMACR = Register(RS=1, Reset=0, Keyhole=0, Cyclic_BD_Enable=0, IOC_IrqEn=0, Dly_IrqEn=0, Err_IrqEn=0, IRQThreshold=1, IRQDelay=0),
  S2MM_DMASR = Register(Halted=0, Idle=1, SGIncld=0, DMAIntErr=0, DMASlvErr=0, DMADecErr=0, SGIntErr=0, SGSlvE

In [10]:
base.axi_dma_0?